In [1]:
from pymongo import MongoClient

In [2]:
client = MongoClient('localhost',27017)

In [3]:
client

MongoClient(host=['localhost:27017'], document_class=dict, tz_aware=False, connect=True)

In [6]:
prin_px = "https://" + "J554696" + ":" + "Aug@2018" + "@pfgproxy.principal.com:80"

In [12]:
import requests
from bs4 import BeautifulSoup
r = requests.get("https://www.sec.gov/Archives/edgar/data/46195/000004619518000025/bankofhawaii10k12312017.htm", proxies={"https":prin_px})

In [11]:
content = r.content

In [13]:
soup = BeautifulSoup(content, 'html.parser')

In [18]:
soup

<document>
<type>10-K
<sequence>1
<filename>bankofhawaii10k12312017.htm
<description>10-K
<text>
<!DOCTYPE html PUBLIC "-//W3C//DTD HTML 4.01 Transitional//EN" "http://www.w3.org/TR/html4/loose.dtd">

<html>
<head>
<!-- Document created using Wdesk 1 -->
<!-- Copyright 2018 Workiva -->
<title>Document</title>
</head>
<body style="font-family:Times New Roman;font-size:10pt;">
<div><a name="sCC6CAC1F43E154788656C7C2CA3DA69C"></a></div><div><div style="line-height:120%;font-size:10pt;"><a href="#s15667A3467575701A78A6E0706FC16A1" style="font-family:inherit;font-size:10pt;"><font style="font-family:inherit;font-size:10pt;">Table of Contents</font></a></div><div style="line-height:120%;font-size:10pt;"><font style="font-family:inherit;font-size:10pt;"><br/></font></div></div><div><br/></div><div style="line-height:120%;padding-bottom:5px;padding-top:5px;text-align:center;font-size:14pt;"><font style="font-family:inherit;font-size:14pt;font-weight:bold;">UNITED STATES<br/>SECURITIES AND EXCH

In [17]:
def split_pages(soup):
    """
    @@ function take inputs as html soup
    and return as list of all splitted pages..
	"""
    file_buffers = soup.prettify().split("\n")
    all_pages = []
    page      = []
    for line in file_buffers:
        line = str(line)
        line1 = line
        if not line: continue
        if line.find("page-break-after:always")!= -1 or line.find("page-break-before: always")!= -1 or line.find("page-break-before") != -1:
            #print line
            page.append(line)
            all_pages.append(" ".join(page[:]))
            page = []
            page_content = []
        else:
            page.append(line)

    return all_pages

In [19]:
all_pages = split_pages(soup)

In [21]:
all_pages[0]

'<document>  <type>   10-K   <sequence>    1    <filename>     bankofhawaii10k12312017.htm     <description>      10-K      <text>       <!DOCTYPE html PUBLIC "-//W3C//DTD HTML 4.01 Transitional//EN" "http://www.w3.org/TR/html4/loose.dtd">       <html>        <head>         <!-- Document created using Wdesk 1 -->         <!-- Copyright 2018 Workiva -->         <title>          Document         </title>        </head>        <body style="font-family:Times New Roman;font-size:10pt;">         <div>          <a name="sCC6CAC1F43E154788656C7C2CA3DA69C">          </a>         </div>         <div>          <div style="line-height:120%;font-size:10pt;">           <a href="#s15667A3467575701A78A6E0706FC16A1" style="font-family:inherit;font-size:10pt;">            <font style="font-family:inherit;font-size:10pt;">             Table of Contents            </font>           </a>          </div>          <div style="line-height:120%;font-size:10pt;">           <font style="font-family:inherit;font-

In [22]:
all_pages = "\n".join(all_pages[1:5])
table_of_content = BeautifulSoup(all_pages, 'html.parser')
tables = table_of_content.findAll( "table")

In [26]:
import re
import pandas as pd
content_table = []

for table in tables:
        all_rows = table.findAll("tr")
        for rows in all_rows:
            row = []
            columns = rows.find_all('td')
            for column in columns:
                txt = str(column.get_text().strip()).lower()
                txt = re.sub( '\s+', ' ', txt ).strip()
                row.append(txt)

            content_table.append(row)
df = pd.DataFrame(content_table)

In [ ]:
def sec_txtFile_parsing(content):
    """
    @@ parse sec text file content
    and extracted header data
    """
    content = str(content)
    content = content.split("\\n")
    header_content = []
    header_flag    = False
    for line in content[:60]:
        line = line.lower()
        if line.find('<SEC-HEADER')!= -1 or line.find('<sec-header')!= -1:
            header_flag = True
            header_content.append(line)
        elif (line.find('</SEC-HEADER')!= -1 or line.find('</sec-header')!= -1) and header_flag:
            header_content.append(line)
            header_flag = False
        elif header_flag:
            header_content.append(line)
    header_dict = processing_header(header_content)
    return header_dict

def processing_header(header_content):
    """
    @@ header content convert into json
    """
    header_dict = {}
    for line in header_content:
        header_info = line.split(":")
        if header_info[0].endswith("hdr.sgml ") or header_info[0].endswith("hdr.sgml") :
            continue
        header_info = list(map(lambda x: x.replace("\\t","\t"),header_info))
        header_info = [header.strip("\t") for header in header_info if header]
        if len(header_info) >1:
            header_dict[header_info[0]] = "@@".join(header_info[1:])
    print (header_dict)
    header_dict["uniqueId"] = header_dict['accession number'].replace('-','')
    return header_dict

def delte_all_metaData():
    """
    @@ Remove all the document from database..
    """
    host,port = read_configfile()
    client = Connection(host,port)
    db = client['pymongo_test']
    posts = db.SEC_FILING
    x = posts.delete_many({})
    print(x.deleted_count, " documents deleted.")

def retrive_metaData():
    """
    @@ retrive metadata on the basis of uniqueId
    """
    host,port = read_configfile()
    print (host,port)

    client = Connection(host,port)
    db = client['pymongo_test']
    posts = db.SEC_FILING

    for post in posts.find({'uniqueId': '000071367618000032'}):
        print ("Hi i am Here::" ,post)

def store_metaData(client,header_data):
    """
    @@ store meta data into mongodb DB name is SEC_FILING
    """
    db = client['pymongo_test']
    posts = db.SEC_FILING
    result = posts.insert_one(header_data)
    if result:
        print('Succesfully Inserted: {0}'.format(result.inserted_id))
    else:
        print('Please Check Mongo Connection \n Mongo Connection Error..')

def metadata_handler(fileContent):
    """
    @@ input take as a fileContent extract header and store into mongodb..
    """
    header_dict = sec_txtFile_parsing(fileContent)
    host,port = read_configfile()
    client = Connection(host,port)
    store_metaData(client,header_dict)
    return header_dict
    #retrive_metaData(client)